# Homework 2

This Notebook will detail Homework 2, which involves a basic capacity expansion model formulation described in [Notebook 3](https://github.com/east-winds/power-systems-optimization/tree/master/Notebooks)

First, load (or install if necessary) a set of packages you'll need for this assignment...

In [1]:
# Uncomment and run this first line if you need to install or update packages
#import Pkg; Pkg.add("JuMP"); Pkg.add("HiGHS"); Pkg.add("DataFrames"); Pkg.add("CSV")
using JuMP
using HiGHS
using DataFrames
using CSV

### Question 1 - Build the basic thermal generation expansion model

Using the example model in [Notebook 3](https://github.com/east-winds/power-systems-optimization/tree/master/Notebooks) as your guide, input the code to create a basic thermal generator capacity expansion model, including [downloading the data for Notebook 3 here](https://github.com/east-winds/power-systems-optimization/tree/master/Notebooks/expansion_data) and loading the appropriate csv files.

In [2]:
# define parameters for generators, demand, and cost of non-served energy
generators = DataFrame(CSV.File("expansion_data_hw/generators_for_expansion.csv"))
demand = DataFrame(CSV.File("expansion_data_hw/demand_for_expansion.csv"))
NSECost = 9000

9000

In [3]:
# define sets (generators - G without the renewables, and hours - H)
G = generators.G[1:(size(generators,1)-2)] 
H = demand.Hour;

In [4]:
# define the model and the optimization solver
Expansion_Model = Model(HiGHS.Optimizer)

A JuMP Model
Feasibility problem with:
Variables: 0
Model mode: AUTOMATIC
CachingOptimizer state: EMPTY_OPTIMIZER
Solver name: HiGHS

In [5]:
# define the decision variables
@variables(Expansion_Model, begin
        CAP[g in G] >=0          # capacity (MW) built for each generator type
        GEN[g in G, h in H] >= 0 # generation (MWh) in each hour 
        NSE[h in H] >= 0         # Non-served energy (MWh) in each hour 
end)

(1-dimensional DenseAxisArray{VariableRef,1,...} with index sets:
    Dimension 1, String7["Geo", "Coal", "CCGT", "CT"]
And data, a 4-element Vector{VariableRef}:
 CAP[Geo]
 CAP[Coal]
 CAP[CCGT]
 CAP[CT], 2-dimensional DenseAxisArray{VariableRef,2,...} with index sets:
    Dimension 1, String7["Geo", "Coal", "CCGT", "CT"]
    Dimension 2, [1, 2, 3, 4, 5, 6, 7, 8, 9, 10  …  8751, 8752, 8753, 8754, 8755, 8756, 8757, 8758, 8759, 8760]
And data, a 4×8760 Matrix{VariableRef}:
 GEN[Geo,1]   GEN[Geo,2]   GEN[Geo,3]   …  GEN[Geo,8759]   GEN[Geo,8760]
 GEN[Coal,1]  GEN[Coal,2]  GEN[Coal,3]     GEN[Coal,8759]  GEN[Coal,8760]
 GEN[CCGT,1]  GEN[CCGT,2]  GEN[CCGT,3]     GEN[CCGT,8759]  GEN[CCGT,8760]
 GEN[CT,1]    GEN[CT,2]    GEN[CT,3]       GEN[CT,8759]    GEN[CT,8760], 1-dimensional DenseAxisArray{VariableRef,1,...} with index sets:
    Dimension 1, [1, 2, 3, 4, 5, 6, 7, 8, 9, 10  …  8751, 8752, 8753, 8754, 8755, 8756, 8757, 8758, 8759, 8760]
And data, a 8760-element Vector{VariableRef}:
 NSE[1]

In [6]:
# define constraints
@constraints(Expansion_Model, begin
    cDemandBalance[h in H], sum(GEN[g,h] for g in G) + NSE[h] == demand.Demand[h] # demand needs to match generation + NSE
    cCapacity[g in G, h in H], GEN[g,h] <= CAP[g] # unable to generate more than the built capacity
end)

(1-dimensional DenseAxisArray{ConstraintRef{Model, MathOptInterface.ConstraintIndex{MathOptInterface.ScalarAffineFunction{Float64}, MathOptInterface.EqualTo{Float64}}, ScalarShape},1,...} with index sets:
    Dimension 1, [1, 2, 3, 4, 5, 6, 7, 8, 9, 10  …  8751, 8752, 8753, 8754, 8755, 8756, 8757, 8758, 8759, 8760]
And data, a 8760-element Vector{ConstraintRef{Model, MathOptInterface.ConstraintIndex{MathOptInterface.ScalarAffineFunction{Float64}, MathOptInterface.EqualTo{Float64}}, ScalarShape}}:
 cDemandBalance[1] : GEN[Geo,1] + GEN[Coal,1] + GEN[CCGT,1] + GEN[CT,1] + NSE[1] = 2274.0
 cDemandBalance[2] : GEN[Geo,2] + GEN[Coal,2] + GEN[CCGT,2] + GEN[CT,2] + NSE[2] = 2581.0
 cDemandBalance[3] : GEN[Geo,3] + GEN[Coal,3] + GEN[CCGT,3] + GEN[CT,3] + NSE[3] = 2576.0
 cDemandBalance[4] : GEN[Geo,4] + GEN[Coal,4] + GEN[CCGT,4] + GEN[CT,4] + NSE[4] = 2482.0
 cDemandBalance[5] : GEN[Geo,5] + GEN[Coal,5] + GEN[CCGT,5] + GEN[CT,5] + NSE[5] = 2396.0
 cDemandBalance[6] : GEN[Geo,6] + GEN[Coal,6] + 

In [7]:
# define objective function
@objective(Expansion_Model, Min,
    sum(generators[generators.G.==g,:FixedCost][1]*CAP[g] + 
        sum(generators[generators.G.==g,:VarCost][1]*GEN[g,h] for h in H)
    for g in G) + 
    sum(NSECost*NSE[h] for h in H) 
);

In [8]:
# Solve the optimization problem
optimize!(Expansion_Model)

Presolving model
43800 rows, 43804 cols, 113880 nonzeros
43800 rows, 43804 cols, 113880 nonzeros
Presolve : Reductions: rows 43800(-0); columns 43804(-0); elements 113880(-0)
Solving the presolved LP
Using EKK dual simplex solver - serial
  Iteration        Objective     Infeasibilities num(sum)
          0     0.0000000000e+00 Pr: 8760(2.25679e+07) 0s
      27493     9.9087397880e+08 Pr: 0(0) 0s
Solving the original LP from the solution after postsolve
Model   status      : Optimal
Simplex   iterations: 27493
Objective value     :  9.9087397880e+08
HiGHS run time      :          0.64


In [9]:
# put capacity and generation into a data frame

# generation
generation = zeros(size(G,1))
for i in 1:size(G,1) 
    generation[i] = sum(value.(GEN)[G[i],:].data) 
end
NSE_gen = sum(value.(NSE).data)
# capacity
capacity = value.(CAP).data
NSE_cap = maximum(value.(NSE).data)

results = DataFrame(
    Resource = G,
    Capacity = capacity,
    Generation = generation
)
# add a row for NSE
push!(results,["NSE" NSE_cap NSE_gen])

5×3 DataFrame
 Row │ Resource  Capacity  Generation     
     │ String7   Float64   Float64        
─────┼────────────────────────────────────
   1 │ Geo            0.0       0.0
   2 │ Coal           0.0       0.0
   3 │ CCGT        3328.0       2.21394e7
   4 │ CT          1290.0  427894.0
   5 │ NSE          195.0     637.0

In [10]:
# calculate total firm generation
firm_generation = sum(generation)
# calculate total built capacity
cap_total = sum(capacity)
print("Firm Generation: ", firm_generation, " Total Cap (MW): ",cap_total)

Firm Generation: 2.256726e7 Total Cap (MW): 4618.0

## Question 2: Analytical solution

**A.** Using the data provided above, sort the demand data from highest to lowest hours to create a load duration curve and save this as a vector/array/DataFrame of your choice.

In [11]:
load_duration_curve = sort(demand.Demand, rev=true)

8760-element Vector{Int64}:
 4813
 4784
 4745
 4677
 4670
 4645
 4629
 4618
 4555
 4514
 4498
 4496
 4496
    ⋮
 1356
 1350
 1349
 1344
 1344
 1337
 1337
 1333
 1326
 1321
 1319
 1306

**B.** Now using the cost data provided in '/generators_for_expansion.csv' and the load duration curve above, use the formulas provided in Lecture to determine an analytical solution to the optimal thermal generation expansion decisions (e.g. solve it algebraically rather than use an optimization solver to find the solution). 

Report the optimal capacity of each generation source and compare to the solution from the optimization model above. 

Show your work in cells below, using Julia to perform calculations. Explain your steps using inline code comments (e.g. `# Comment`) or by interspersing Markdown cells.  

Tip: round your solutions for the crossover hour between each technology to the nearest integer (as we have discrete hours in the time series).

In [12]:
# ignore renewables for now 
# Baseload: Coal, Load Tracking: CCGT, Peaker: CT
# define constants
# Annuitized investment
I_Coal = generators.Annuity[2]
I_CCGT = generators.Annuity[3]
I_CT = generators.Annuity[4]
# fixed O and M
F_Coal = generators.FixedOM[2]
F_CCGT = generators.FixedOM[3]
F_CT = generators.FixedOM[4]
# variable cost
V_Coal = generators.VarCost[2]
V_CCGT = generators.VarCost[3]
V_CT = generators.VarCost[4]
CNSE = 9000

9000

In [13]:
# Plot to visualize the intersections for each technology:
using Plots; plotly()

coal = (V_Coal*demand.Hour) .+ (I_Coal + F_Coal)
ccgt = (V_CCGT*demand.Hour) .+ (I_CCGT + F_CCGT)
ct = (V_CT*demand.Hour) .+ (I_CT + F_CT)
nonserved = CNSE*demand.Hour

plot(range(0,8760,length=8760),[coal,ccgt,ct,nonserved], ylims=(0,500000), xlims=(0,8760), label = ["Coal" "CCGT" "CT" "NSE"])
xaxis!("Hours of Utilization")
yaxis!("Total Cost per Unit")

┌ Info: For saving to png with the Plotly backend PlotlyBase and PlotlyKaleido need to be installed.
└ @ Plots /Users/haydenburt/.julia/packages/Plots/W75kY/src/backends.jl:319


In [14]:
# calculate hours for each type
h_NSE = Int(round((I_CT + F_CT)/(CNSE-V_CT))) # hours of non-served energy
h_CT = Int(round((I_CCGT + F_CCGT - I_CT - F_CT)/(V_CT - V_CCGT))) # hours of CT
h_CCGT = 8760 # hours of CCGT

# Coal is above (more expensive) for all hours in the year - so I am not allocating any hours to coal
# Therefore, CCGT is essentially the baseload

8760

In [15]:
# find capacity using intersection of hours on demand curve (subtract for areas in between lines defined by each h on curve)
k_CT = load_duration_curve[h_NSE]-load_duration_curve[h_CT] 
k_CCGT = load_duration_curve[h_CT]
k_NSE = load_duration_curve[1]-load_duration_curve[h_NSE]

AnalyticalSol = DataFrame(G = ["CT","CCGT","Coal","NSE"], hours = [h_CT,h_CCGT,0,h_NSE], capacity = [k_CT,k_CCGT,0,k_NSE])

4×3 DataFrame
 Row │ G       hours  capacity 
     │ String  Int64  Int64    
─────┼─────────────────────────
   1 │ CT       1204      1301
   2 │ CCGT     8760      3328
   3 │ Coal        0         0
   4 │ NSE         7       184

**C.** Now change the fuel cost of natural gas to \$8.00/MMBtu, recalculate the variable cost of CCGTs and CTs, and solve again for the optimal generation capacity mix. Describe what changes in your capacity results and what doesn't, and provide an explanation.

In [16]:
# Update variable costs for CT and CCGT
V_CCGT = generators.VarOM[3]+generators.HeatRate[3]*8
V_CT = generators.VarOM[4]+generators.HeatRate[4]*8

82.6

In [17]:
# Plot to visualize the intersections for each technology:
using Plots; plotly()

coal = (V_Coal*demand.Hour) .+ (I_Coal + F_Coal)
ccgt = (V_CCGT*demand.Hour) .+ (I_CCGT + F_CCGT)
ct = (V_CT*demand.Hour) .+ (I_CT + F_CT)
nonserved = CNSE*demand.Hour

plot(range(0,8760,length=8760),[coal,ccgt,ct,nonserved], ylims=(0,500000), xlims=(0,8760), label = ["Coal" "CCGT" "CT" "NSE"])
xaxis!("Hours of Utilization")
yaxis!("Total Cost per Unit")

In [18]:
# calculate hours for each type
h_NSE = Int(round((I_CT + F_CT)/(CNSE-V_CT))) # hours of non-served energy
h_CT = Int(round((I_CCGT + F_CCGT - I_CT - F_CT)/(V_CT - V_CCGT))) # hours of CT
h_CCGT = Int(round((I_Coal + F_Coal - I_CCGT - F_CCGT)/(V_CCGT - V_Coal))) # hours of CCGT
h_Coal = 8760
# Coal is above for all hours - so I am not allocating any hours to coal
# Therefore, CCGT is essentially the baseload

8760

In [19]:
# find capacity using intersection of hours on demand curve
k_CT = load_duration_curve[h_NSE]-load_duration_curve[h_CT]
k_CCGT = load_duration_curve[h_CT]-load_duration_curve[h_CCGT]
k_Coal = load_duration_curve[h_CCGT]
k_NSE = load_duration_curve[1]-load_duration_curve[h_NSE]

AnalyticalSol = DataFrame(G = ["CT","CCGT","Coal", "NSE"], hours = [h_CT,h_CCGT,h_Coal,h_NSE], capacity = [k_CT,k_CCGT,k_Coal,k_NSE])


4×3 DataFrame
 Row │ G       hours  capacity 
     │ String  Int64  Int64    
─────┼─────────────────────────
   1 │ CT        664      1047
   2 │ CCGT     6479      1472
   3 │ Coal     8760      2110
   4 │ NSE         7       184

Since the increase in the fuel cost for the natural gas was introduced, it changed the variable costs for CT and CCGT. Prior to this, the coal was more expensive at all hours of utilization than either option, meaning that no capacity was built for coal. However, with the increased price of natural gas, coal became the baseload as it had the lowest variable cost. As a result, the capacity for both CCGT (now the load following plant) and CT (now the peaker plant) decreased. The hours and capacity of non-served energy did not change.

## Question 3 - Expansion with renewables

**A.** Using JuMP/Julia, implement an optimization model based on the formulation for optimal thermal+renewable capacity expansion provided in Section 2 of [Notebook 3](https://github.com/east-winds/power-systems-optimization/tree/master/Notebooks). 

In [20]:
# add in hourly capacity factor for renewables
capacity_factor = DataFrame(CSV.File("expansion_data_hw/wind_solar_for_expansion.csv"))
# update list of generators to include renewables
G = generators.G

6-element Vector{String7}:
 "Geo"
 "Coal"
 "CCGT"
 "CT"
 "Wind"
 "Solar"

In [21]:
Expansion_Model_Renewables = Model(HiGHS.Optimizer)

A JuMP Model
Feasibility problem with:
Variables: 0
Model mode: AUTOMATIC
CachingOptimizer state: EMPTY_OPTIMIZER
Solver name: HiGHS

In [22]:
@variables(Expansion_Model_Renewables, begin
        CAP[g in G] >= 0 # built capacity (MW)
        GEN[g in G, h in H] >= 0 #generation (MWh) in each hour
        NSE[h in H] >= 0 # non-served energy (MWh) in each hour
    end)

(1-dimensional DenseAxisArray{VariableRef,1,...} with index sets:
    Dimension 1, String7["Geo", "Coal", "CCGT", "CT", "Wind", "Solar"]
And data, a 6-element Vector{VariableRef}:
 CAP[Geo]
 CAP[Coal]
 CAP[CCGT]
 CAP[CT]
 CAP[Wind]
 CAP[Solar], 2-dimensional DenseAxisArray{VariableRef,2,...} with index sets:
    Dimension 1, String7["Geo", "Coal", "CCGT", "CT", "Wind", "Solar"]
    Dimension 2, [1, 2, 3, 4, 5, 6, 7, 8, 9, 10  …  8751, 8752, 8753, 8754, 8755, 8756, 8757, 8758, 8759, 8760]
And data, a 6×8760 Matrix{VariableRef}:
 GEN[Geo,1]    GEN[Geo,2]    …  GEN[Geo,8759]    GEN[Geo,8760]
 GEN[Coal,1]   GEN[Coal,2]      GEN[Coal,8759]   GEN[Coal,8760]
 GEN[CCGT,1]   GEN[CCGT,2]      GEN[CCGT,8759]   GEN[CCGT,8760]
 GEN[CT,1]     GEN[CT,2]        GEN[CT,8759]     GEN[CT,8760]
 GEN[Wind,1]   GEN[Wind,2]      GEN[Wind,8759]   GEN[Wind,8760]
 GEN[Solar,1]  GEN[Solar,2]  …  GEN[Solar,8759]  GEN[Solar,8760], 1-dimensional DenseAxisArray{VariableRef,1,...} with index sets:
    Dimension 1, [1

In [23]:
# define constraints
@constraints(Expansion_Model_Renewables, begin
        cDemandBalance[h in H], sum(GEN[g,h] for g in G) + NSE[h] == demand.Demand[h]
        cCapacityNonRenewable[g in G[1:(size(generators,1)-2)], h in H], GEN[g,h] <= CAP[g]
        cCapacityRenewable[g in G[(size(generators,1)-1):(size(generators,1))], h in H], GEN[g,h] <= CAP[g].*capacity_factor[h,g]
    end)

(1-dimensional DenseAxisArray{ConstraintRef{Model, MathOptInterface.ConstraintIndex{MathOptInterface.ScalarAffineFunction{Float64}, MathOptInterface.EqualTo{Float64}}, ScalarShape},1,...} with index sets:
    Dimension 1, [1, 2, 3, 4, 5, 6, 7, 8, 9, 10  …  8751, 8752, 8753, 8754, 8755, 8756, 8757, 8758, 8759, 8760]
And data, a 8760-element Vector{ConstraintRef{Model, MathOptInterface.ConstraintIndex{MathOptInterface.ScalarAffineFunction{Float64}, MathOptInterface.EqualTo{Float64}}, ScalarShape}}:
 cDemandBalance[1] : GEN[Geo,1] + GEN[Coal,1] + GEN[CCGT,1] + GEN[CT,1] + GEN[Wind,1] + GEN[Solar,1] + NSE[1] = 2274.0
 cDemandBalance[2] : GEN[Geo,2] + GEN[Coal,2] + GEN[CCGT,2] + GEN[CT,2] + GEN[Wind,2] + GEN[Solar,2] + NSE[2] = 2581.0
 cDemandBalance[3] : GEN[Geo,3] + GEN[Coal,3] + GEN[CCGT,3] + GEN[CT,3] + GEN[Wind,3] + GEN[Solar,3] + NSE[3] = 2576.0
 cDemandBalance[4] : GEN[Geo,4] + GEN[Coal,4] + GEN[CCGT,4] + GEN[CT,4] + GEN[Wind,4] + GEN[Solar,4] + NSE[4] = 2482.0
 cDemandBalance[5] : G

In [24]:
# define objective 
@objective(Expansion_Model_Renewables, Min,
    sum(generators[generators.G.==g,:FixedCost][1]*CAP[g] + 
        sum(generators[generators.G.==g,:VarCost][1]*GEN[g,h] for h in H)
    for g in G) + 
    sum(NSECost*NSE[h] for h in H) 
);

**B.** Solve the model to determine the optimal capacity when wind and solar are available resources and extract results for generation and capacity.

In [25]:
optimize!(Expansion_Model_Renewables)

Presolving model
56856 rows, 56862 cols, 153048 nonzeros
56856 rows, 56862 cols, 153048 nonzeros
Presolve : Reductions: rows 56856(-4464); columns 56862(-4464); elements 153048(-8928)
Solving the presolved LP
Using EKK dual simplex solver - serial
  Iteration        Objective     Infeasibilities num(sum)
          0     0.0000000000e+00 Pr: 8760(6.18517e+06) 0s
      40369     8.2899893531e+08 Pr: 0(0); Du: 0(3.19744e-13) 3s
Solving the original LP from the solution after postsolve
Model   status      : Optimal
Simplex   iterations: 40369
Objective value     :  8.2899893531e+08
HiGHS run time      :          3.93


In [26]:
# extract generation in MWh
generation = zeros(size(G,1))
for i in 1:size(G,1) 
    generation[i] = sum(value.(GEN)[G[i],:].data) 
end
NSE_gen = sum(value.(NSE).data)

# extract built capacity in MW
capacity = value.(CAP).data
NSE_cap = maximum(value.(NSE).data)

# put built capacity, generation, and % capacity and generation in data frame
results = DataFrame(
    Resource = G,
    Built_Capacity = capacity,
    Generation = generation,
)

# add a row for NSE
push!(results, ["NSE" NSE_cap NSE_gen])

7×3 DataFrame
 Row │ Resource  Built_Capacity  Generation  
     │ String7   Float64         Float64     
─────┼───────────────────────────────────────
   1 │ Geo                0.0      0.0
   2 │ Coal               0.0      0.0
   3 │ CCGT            2422.86     1.13677e7
   4 │ CT              1419.78     4.5398e5
   5 │ Wind             349.956    1.0077e6
   6 │ Solar           3362.77     9.73816e6
   7 │ NSE              136.513  399.328

**C.** What happens to the total firm generation and maximum MW of non-served energy? What does this imply about the capacity value of solar and/or wind built in the optimal capacity mix?

In [27]:
# calculate total firm generation
generation_firm = sum(generation[1:(size(generation,1)-2)])
# calculate total capacity of renewables and non-renewables
cap_renewables = sum(capacity[5:6])
cap_non_renewables = sum(capacity[1:4])
# calculate capacity value (How many MW of CT/Coal/CCGT are replaced by 1MW of Solar/Wind)
# use "cap_total" from Question 1
cap_value = (cap_total-cap_non_renewables)/(cap_renewables)

print("Firm Generation: ",generation_firm)
print(" Capacity Nonrenewables: ",cap_non_renewables)
print(" Capacity Renewables: ",cap_renewables)
print(" Capacity Value: ",cap_value)

Firm Generation: 1.1821636392813765e7 Capacity Nonrenewables: 3842.6387856796537 Capacity Renewables: 3712.723799795235 Capacity Value: 0.2088389161518315

The total firm generation is almost halved as it decreases from 2.26e7 MWh in the case without renewables to only 1.18e7 MWh when renewables are added to the scenario. 

The maximum MW of nonserved energy also decreases from 195 MW in the no renewables case to about 137 MW in the renewables case.

In the case where there are no renewables, the total built capacity is 4618 MW. For the case with renewables, the total built capacity is 3843 MW of non-renewables and 3713 MW of renewables. Therefore, 3713 MW of renewables replaces 775 MW of non-renewables. If the capacity value of solar/wind refers to how many MW of non-renewables can be replaced by one MW of solar/wind capacity, then the capacity value in this  scenario is 21%.

## Question 4: Brownfield Expansion Model

**A.** Now implement an optimization model based on the formulation for optimal "brownfield" thermal+renewable capacity expansion (e.g. with existing generators) provided in Section 3 of [Notebook 3](https://github.com/east-winds/power-systems-optimization/tree/master/Notebooks).

Use the following data for fixed and variable costs of existing gas capacity. Note: unlike in the formulation in Notebook 3, there is no existing renewable capacity here to consider (only thermal).

In [28]:
# Load new generator options
#path = joinpath([REPLACE THIS WITH PATH TO YOUR power-systems-optimization DIRECTORY HERE],"Notebooks","expansion_data")
path = joinpath("/Users/haydenburt/Documents/GitHub/power-systems-optimization","Notebooks","expansion_data")
generators = DataFrame(CSV.File(joinpath(path,"generators_for_expansion.csv")))
# Add parameters for existing CCGTs, with the set index "Old"
push!(generators, ["Old_CC" "Existing CCGT" 0 40000 5 7.5 4 0 0 0 0 40000 30])
# Add parameters for existing CTs, with the set index "Old"
push!(generators, ["Old_CT" "Existing CT" 0 30000 11 11.0 4 0 0 0 0 30000 55])

# Set installed capacity for existing CCGTs:
ExistingCap_CCGT = 1260 # Approximate actual existing capacity in SDGE
ExistingCap_CT = 925 # Approximate actual existing capacity in SDGE
# Add new column to generators Data Frame
generators[!,:ExistingCap] = [0,0,0,0,0,0, ExistingCap_CCGT, ExistingCap_CT];


In [29]:
# create model
Expansion_Model_Brown = Model(HiGHS.Optimizer)

A JuMP Model
Feasibility problem with:
Variables: 0
Model mode: AUTOMATIC
CachingOptimizer state: EMPTY_OPTIMIZER
Solver name: HiGHS

In [30]:
# define new sets and subsets
G = generators.G
G_new = G[1:6] # subset for all new/built generators
G_old = G[7:8] # subset for all old/existing generators
G_built_thermal = G[1:4] # subset for new thermal
G_built_renew = G[5:6] # subset for new renewables

2-element Vector{String7}:
 "Wind"
 "Solar"

In [31]:
# define decision variables
@variables(Expansion_Model_Brown, begin
        CAP[g in G_new] >= 0 # built capacity (MW)
        RET[g in G_old] >= 0 # retired capacity (MW)
        GEN[g in G, h in H] >= 0 #generation (MWh) in each hour
        NSE[h in H] >= 0 # non-served energy (MWh) in each hour
    end)

(1-dimensional DenseAxisArray{VariableRef,1,...} with index sets:
    Dimension 1, String7["Geo", "Coal", "CCGT", "CT", "Wind", "Solar"]
And data, a 6-element Vector{VariableRef}:
 CAP[Geo]
 CAP[Coal]
 CAP[CCGT]
 CAP[CT]
 CAP[Wind]
 CAP[Solar], 1-dimensional DenseAxisArray{VariableRef,1,...} with index sets:
    Dimension 1, String7["Old_CC", "Old_CT"]
And data, a 2-element Vector{VariableRef}:
 RET[Old_CC]
 RET[Old_CT], 2-dimensional DenseAxisArray{VariableRef,2,...} with index sets:
    Dimension 1, String7["Geo", "Coal", "CCGT", "CT", "Wind", "Solar", "Old_CC", "Old_CT"]
    Dimension 2, [1, 2, 3, 4, 5, 6, 7, 8, 9, 10  …  8751, 8752, 8753, 8754, 8755, 8756, 8757, 8758, 8759, 8760]
And data, a 8×8760 Matrix{VariableRef}:
 GEN[Geo,1]     GEN[Geo,2]     …  GEN[Geo,8759]     GEN[Geo,8760]
 GEN[Coal,1]    GEN[Coal,2]       GEN[Coal,8759]    GEN[Coal,8760]
 GEN[CCGT,1]    GEN[CCGT,2]       GEN[CCGT,8759]    GEN[CCGT,8760]
 GEN[CT,1]      GEN[CT,2]         GEN[CT,8759]      GEN[CT,8760]
 G

In [32]:
# define constraints
@constraints(Expansion_Model_Brown, begin
        cDemandBalance[h in H], sum(GEN[g,h] for g in G) + NSE[h] == demand.Demand[h]
        cCapNewThermal[g in G_built_thermal, h in H], GEN[g,h] <= CAP[g]
        cCapOldThermal[g in G_old, h in H], GEN[g,h] <= generators[generators.G.==g,:ExistingCap][1] - RET[g]
        cCapNewRenewable[g in G_built_renew, h in H], GEN[g,h] <= CAP[g].*capacity_factor[h,g]
    end)

(1-dimensional DenseAxisArray{ConstraintRef{Model, MathOptInterface.ConstraintIndex{MathOptInterface.ScalarAffineFunction{Float64}, MathOptInterface.EqualTo{Float64}}, ScalarShape},1,...} with index sets:
    Dimension 1, [1, 2, 3, 4, 5, 6, 7, 8, 9, 10  …  8751, 8752, 8753, 8754, 8755, 8756, 8757, 8758, 8759, 8760]
And data, a 8760-element Vector{ConstraintRef{Model, MathOptInterface.ConstraintIndex{MathOptInterface.ScalarAffineFunction{Float64}, MathOptInterface.EqualTo{Float64}}, ScalarShape}}:
 cDemandBalance[1] : GEN[Geo,1] + GEN[Coal,1] + GEN[CCGT,1] + GEN[CT,1] + GEN[Wind,1] + GEN[Solar,1] + GEN[Old_CC,1] + GEN[Old_CT,1] + NSE[1] = 2274.0
 cDemandBalance[2] : GEN[Geo,2] + GEN[Coal,2] + GEN[CCGT,2] + GEN[CT,2] + GEN[Wind,2] + GEN[Solar,2] + GEN[Old_CC,2] + GEN[Old_CT,2] + NSE[2] = 2581.0
 cDemandBalance[3] : GEN[Geo,3] + GEN[Coal,3] + GEN[CCGT,3] + GEN[CT,3] + GEN[Wind,3] + GEN[Solar,3] + GEN[Old_CC,3] + GEN[Old_CT,3] + NSE[3] = 2576.0
 cDemandBalance[4] : GEN[Geo,4] + GEN[Coal,4]

In [33]:
# define the objective 
@objective(Expansion_Model_Brown, Min,
    sum(generators[generators.G.==g,:FixedCost][1]*CAP[g]
    for g in G_new) + sum(generators[generators.G.==g,:FixedCost][1]*
        (generators[generators.G.==g,:ExistingCap][1]-RET[g]) for g in G_old)+
    sum(sum(generators[generators.G.==g,:VarCost][1]*GEN[g,h] for h in H) for g in G) +
    sum(NSECost*NSE[h] for h in H) 
);

**B.** Solve the model to determine the optimal capacity when with existing generators and extract results for generation and capacity (including retirements).

In [34]:
optimize!(Expansion_Model_Brown)

Presolving model
74376 rows, 74384 cols, 205608 nonzeros
74376 rows, 74384 cols, 205608 nonzeros
Presolve : Reductions: rows 74376(-4464); columns 74384(-4464); elements 205608(-8928)
Solving the presolved LP
Using EKK dual simplex solver - serial
  Iteration        Objective     Infeasibilities num(sum)
          0    -6.9997808764e+04 Ph1: 17520(10432); Du: 2(69997.8) 0s
      46226     7.5415721793e+08 Pr: 1101(77328.2); Du: 0(6.45801e-08) 5s
      47723     7.5494110973e+08 Pr: 0(0); Du: 0(5.12301e-12) 5s
Solving the original LP from the solution after postsolve
Model   status      : Optimal
Simplex   iterations: 47723
Objective value     :  7.5494110973e+08
HiGHS run time      :          5.90


In [35]:
# extract generation in MWh
generation = zeros(size(G,1))
for i in 1:size(G,1) 
    generation[i] = sum(value.(GEN)[G[i],:].data) 
end
NSE_gen = sum(value.(NSE).data)

# extract built capacity in MW
capacity = value.(CAP).data 
NSE_cap = maximum(value.(NSE).data)

# extract retired capacity
retired = value.(RET).data

# put built capacity, generation, and % capacity and generation in data frame
results = DataFrame(
    Resource = G,
    Built_Capacity = [capacity; 0; 0],
    Retired_Capacity = [0;0;0;0;0;0; retired],
    Generation = generation
)

# add a row for NSE
push!(results, ["NSE" NSE_cap 0 NSE_gen])

9×4 DataFrame
 Row │ Resource  Built_Capacity  Retired_Capacity  Generation     
     │ String7   Float64         Float64           Float64        
─────┼────────────────────────────────────────────────────────────
   1 │ Geo                0.0                 0.0       0.0
   2 │ Coal               0.0                 0.0       0.0
   3 │ CCGT            1417.31                0.0       8.54501e6
   4 │ CT               238.555               0.0       1.05948e5
   5 │ Wind             385.045               0.0       1.1093e6
   6 │ Solar           3357.62                0.0       9.72026e6
   7 │ Old_CC             0.0                 0.0       2.9734e6
   8 │ Old_CT             0.0                 0.0  113611.0
   9 │ NSE              125.066               0.0     366.094